In [1]:
import gym
import numpy as np
rm='Pong-v0'

In [2]:
%matplotlib inline
from matplotlib import animation
import matplotlib.pyplot as plt
from IPython.display import display, HTML

def display_frames_as_gif(frames):
    plt.figure(figsize=(frames[0].shape[1] / 72.0, frames[0].shape[0] / 72.0), dpi = 144)
    patch = plt.imshow(frames[0])
    plt.axis('off')
    def animate(i):
        patch.set_data(frames[i])
    anim = animation.FuncAnimation(plt.gcf(), animate, frames = len(frames), interval=50)
    plt.close(anim._fig)
    display(HTML(anim.to_jshtml()))

from gym.wrappers import AtariPreprocessing
gym.new_step_api=True
env = gym.make(rm)

H = 200 # number of hidden layer neurons
D = 80 * 80 # input dimensionality: 80x80 grid
model = {}
model['W1'] = np.random.randn(H,D) / np.sqrt(D) # "Xavier" initialization
model['W2'] = np.random.randn(H) / np.sqrt(H)
# hyperparameters
batch_size = 10 # every how many episodes to do a param update?
learning_rate = 1e-3
gamma = 0.99 # discount factor for reward
decay_rate = 0.99 # decay factor for RMSProp leaky sum of grad^2
grad_buffer = { k : np.zeros_like(v) for k,v in model.items() } # update buffers that add up gradients over a batch
rmsprop_cache = { k : np.zeros_like(v) for k,v in model.items() } # rmsprop memory

def sigmoid(x): 
  return 1.0 / (1.0 + np.exp(-x)) # sigmoid "squashing" function to interval [0,1]

def prepro(I):
  I=np.asarray(I)
  I = I[35:195] # crop
  I = I[::2,::2,0] # downsample by factor of 2
  
  I[I == 144] = 0 # erase background (background type 1)
  
  I[I == 109] = 0 # erase background (background type 2)
  
  I[I != 0] = 1 # everything else (paddles, ball) just set to 1
  return I.astype(float).ravel()

def discount_rewards(r):
  discounted_r = np.zeros_like(r)
  running_add = 0
  for t in reversed(range(0, r.size)):
    if r[t] != 0: running_add = 0 # reset the sum, since this was a game boundary (pong specific!)
    running_add = running_add * gamma + r[t]
    discounted_r[t] = running_add
  return discounted_r

def policy_forward(x):
  h = np.dot(model['W1'], x)
  h[h<0] = 0 # ReLU nonlinearity
  logp = np.dot(model['W2'], h)
  p = sigmoid(logp)
  return p, h # return probability of taking action 2, and hidden state

def policy_backward(epx, eph, epdlogp):
  """ backward pass. (eph is array of intermediate hidden states) """
  dW2 = np.dot(eph.T, epdlogp).ravel()
  dh = np.outer(epdlogp, model['W2'])
  dh[eph <= 0] = 0 # backpro prelu
  dW1 = np.dot(dh.T, epx)
  return {'W1':dW1, 'W2':dW2}

def model_step(model, observation, prev_x):

  cur_x = prepro(observation)
  x = cur_x - prev_x if prev_x is not None else np.zeros(D)
  prev_x = cur_x
  
  # forward the policy network and sample an action from the returned probability
  aprob, _ = policy_forward(x)
  action = 2 if aprob >= 0.5 else 3 # roll the dice!
  
  return action, prev_x

def play_game(env, model):
  observation = env.reset()

  frames = []
  cumulated_reward = 0

  prev_x = None # used in computing the difference frame

  for t in range(1000):
      frames.append(env.render(mode = 'rgb_array'))
      action, prev_x = model_step(model, observation, prev_x)
      observation, reward, done, info = env.step(action)
      cumulated_reward += reward
      if done:
          print("Episode finished after {} timesteps, accumulated reward = {}".format(t+1, cumulated_reward))
          break
  print("Episode finished without success, accumulated reward = {}".format(cumulated_reward))
  env.close()
  display_frames_as_gif(frames)

def train_model(env, model, total_episodes = 100):
  hist = []
  observation = env.reset()

  prev_x = None # used in computing the difference frame
  xs,hs,dlogps,drs = [],[],[],[]
  running_reward = None
  reward_sum = 0
  episode_number = 0

  while True:
  
    cur_x = prepro(observation)
    x = cur_x - prev_x if prev_x is not None else np.zeros(D)
    prev_x = cur_x

    # forward the policy network and sample an action from the returned probability
    aprob, h = policy_forward(x)
    action = 2 if np.random.uniform() < aprob else 3 # roll the dice!

    # record various intermediates (needed later for backprop)
    xs.append(x) # observation
    hs.append(h) # hidden state
    y = 1 if action == 2 else 0 # a "fake label"
    dlogps.append(y - aprob) # grad that encourages the action that was taken to be taken (see http://cs231n.github.io/neural-networks-2/#losses if confused)

    # step the environment and get new measurements
    observation, reward, done, info = env.step(action)
    reward_sum += reward

    drs.append(reward) # record reward (has to be done after we call step() to get reward for previous action)

    if done: # an episode finished
      episode_number += 1

      # stack together all inputs, hidden states, action gradients, and rewards for this episode
      epx = np.vstack(xs)
      eph = np.vstack(hs)
      epdlogp = np.vstack(dlogps)
      epr = np.vstack(drs)
      xs,hs,dlogps,drs = [],[],[],[] # reset array memory

      # compute the discounted reward backwards through time
      discounted_epr = discount_rewards(epr)
      # standardize the rewards to be unit normal (helps control the gradient estimator variance)
      discounted_epr -= np.mean(discounted_epr)
      discounted_epr /= np.std(discounted_epr)

      epdlogp *= discounted_epr # modulate the gradient with advantage (PG magic happens right here.)
      grad = policy_backward(epx, eph, epdlogp)
      for k in model: grad_buffer[k] += grad[k] # accumulate grad over batch

      # perform rmsprop parameter update every batch_size episodes
      if episode_number % batch_size == 0:
        for k,v in model.items():
          g = grad_buffer[k] # gradient
          rmsprop_cache[k] = decay_rate * rmsprop_cache[k] + (1 - decay_rate) * g**2
          model[k] += learning_rate * g / (np.sqrt(rmsprop_cache[k]) + 1e-5)
          grad_buffer[k] = np.zeros_like(v) # reset batch gradient buffer

      # boring book-keeping
      running_reward = reward_sum if running_reward is None else running_reward * 0.99 + reward_sum * 0.01
      hist.append((episode_number, reward_sum, running_reward))
      print ('episode %f, reward total was %f. running mean: %f' % (episode_number, reward_sum, running_reward))
      reward_sum = 0
      observation = env.reset() # reset env
      prev_x = None
      if episode_number == total_episodes: 
        return hist

    # if reward != 0: # Pong has either +1 or -1 reward exactly when game ends.
    #   print('ep {}: game finished, reward: {}'.format(episode_number, reward) + ('' if reward == -1 else ' !!!!!!!!'))

C:\Users\User\AppData\Local\Programs\Python\Python310\lib\site-packages\gym\envs\registration.py:592: UserWarning: WARN: The environment Pong-v0 is out of date. You should consider upgrading to version `v4`.
  logger.warn(
C:\Users\User\AppData\Local\Programs\Python\Python310\lib\site-packages\gym\core.py:329: DeprecationWarning: WARN: Initializing wrapper in old step API which returns one bool instead of two. It is recommended to set `new_step_api=True` to use new step API. This will be the default behaviour in future.
  deprecation(
C:\Users\User\AppData\Local\Programs\Python\Python310\lib\site-packages\gym\wrappers\step_api_compatibility.py:39: DeprecationWarning: WARN: Initializing environment in old step API which returns one bool instead of two. It is recommended to set `new_step_api=True` to use new step API. This will be the default behaviour in future.
  deprecation(


In [3]:
%time hist1 = train_model(env, model, total_episodes=6000)

C:\Users\User\AppData\Local\Programs\Python\Python310\lib\site-packages\gym\utils\passive_env_checker.py:227: DeprecationWarning: WARN: Core environment is written in old step API which returns one bool instead of two. It is recommended to rewrite the environment with new step API. 
  logger.deprecation(


episode 1.000000, reward total was -21.000000. running mean: -21.000000
episode 2.000000, reward total was -21.000000. running mean: -21.000000
episode 3.000000, reward total was -21.000000. running mean: -21.000000
episode 4.000000, reward total was -21.000000. running mean: -21.000000
episode 5.000000, reward total was -21.000000. running mean: -21.000000
episode 6.000000, reward total was -20.000000. running mean: -20.990000
episode 7.000000, reward total was -21.000000. running mean: -20.990100
episode 8.000000, reward total was -21.000000. running mean: -20.990199
episode 9.000000, reward total was -18.000000. running mean: -20.960297
episode 10.000000, reward total was -21.000000. running mean: -20.960694
episode 11.000000, reward total was -20.000000. running mean: -20.951087
episode 12.000000, reward total was -19.000000. running mean: -20.931576
episode 13.000000, reward total was -19.000000. running mean: -20.912260
episode 14.000000, reward total was -21.000000. running mean

episode 114.000000, reward total was -20.000000. running mean: -20.350904
episode 115.000000, reward total was -19.000000. running mean: -20.337395
episode 116.000000, reward total was -19.000000. running mean: -20.324021
episode 117.000000, reward total was -21.000000. running mean: -20.330781
episode 118.000000, reward total was -21.000000. running mean: -20.337473
episode 119.000000, reward total was -20.000000. running mean: -20.334098
episode 120.000000, reward total was -19.000000. running mean: -20.320758
episode 121.000000, reward total was -21.000000. running mean: -20.327550
episode 122.000000, reward total was -19.000000. running mean: -20.314274
episode 123.000000, reward total was -20.000000. running mean: -20.311132
episode 124.000000, reward total was -21.000000. running mean: -20.318020
episode 125.000000, reward total was -20.000000. running mean: -20.314840
episode 126.000000, reward total was -19.000000. running mean: -20.301692
episode 127.000000, reward total was -

episode 225.000000, reward total was -21.000000. running mean: -20.074312
episode 226.000000, reward total was -18.000000. running mean: -20.053569
episode 227.000000, reward total was -21.000000. running mean: -20.063033
episode 228.000000, reward total was -19.000000. running mean: -20.052403
episode 229.000000, reward total was -19.000000. running mean: -20.041879
episode 230.000000, reward total was -16.000000. running mean: -20.001460
episode 231.000000, reward total was -19.000000. running mean: -19.991445
episode 232.000000, reward total was -19.000000. running mean: -19.981531
episode 233.000000, reward total was -19.000000. running mean: -19.971716
episode 234.000000, reward total was -20.000000. running mean: -19.971999
episode 235.000000, reward total was -19.000000. running mean: -19.962279
episode 236.000000, reward total was -21.000000. running mean: -19.972656
episode 237.000000, reward total was -20.000000. running mean: -19.972929
episode 238.000000, reward total was -

episode 336.000000, reward total was -18.000000. running mean: -19.627505
episode 337.000000, reward total was -20.000000. running mean: -19.631230
episode 338.000000, reward total was -20.000000. running mean: -19.634917
episode 339.000000, reward total was -14.000000. running mean: -19.578568
episode 340.000000, reward total was -20.000000. running mean: -19.582783
episode 341.000000, reward total was -21.000000. running mean: -19.596955
episode 342.000000, reward total was -20.000000. running mean: -19.600985
episode 343.000000, reward total was -21.000000. running mean: -19.614975
episode 344.000000, reward total was -20.000000. running mean: -19.618826
episode 345.000000, reward total was -20.000000. running mean: -19.622637
episode 346.000000, reward total was -19.000000. running mean: -19.616411
episode 347.000000, reward total was -16.000000. running mean: -19.580247
episode 348.000000, reward total was -21.000000. running mean: -19.594444
episode 349.000000, reward total was -

...

episode 5467.000000, reward total was -1.000000. running mean: -4.180004
episode 5468.000000, reward total was -11.000000. running mean: -4.248204
episode 5469.000000, reward total was 5.000000. running mean: -4.155722
episode 5470.000000, reward total was -3.000000. running mean: -4.144165
episode 5471.000000, reward total was -4.000000. running mean: -4.142723
episode 5472.000000, reward total was -6.000000. running mean: -4.161296
episode 5473.000000, reward total was -2.000000. running mean: -4.139683
episode 5474.000000, reward total was 5.000000. running mean: -4.048286
episode 5475.000000, reward total was 5.000000. running mean: -3.957804
episode 5476.000000, reward total was 2.000000. running mean: -3.898226
episode 5477.000000, reward total was 9.000000. running mean: -3.769243
episode 5478.000000, reward total was -8.000000. running mean: -3.811551
episode 5479.000000, reward total was 10.000000. running mean: -3.673435
episode 5480.000000, reward total was -9.000000. runnin

episode 5580.000000, reward total was 1.000000. running mean: -2.502850
episode 5581.000000, reward total was -6.000000. running mean: -2.537821
episode 5582.000000, reward total was -3.000000. running mean: -2.542443
episode 5583.000000, reward total was 1.000000. running mean: -2.507019
episode 5584.000000, reward total was -2.000000. running mean: -2.501948
episode 5585.000000, reward total was 3.000000. running mean: -2.446929
episode 5586.000000, reward total was 1.000000. running mean: -2.412460
episode 5587.000000, reward total was -7.000000. running mean: -2.458335
episode 5588.000000, reward total was 1.000000. running mean: -2.423752
episode 5589.000000, reward total was 10.000000. running mean: -2.299514
episode 5590.000000, reward total was 2.000000. running mean: -2.256519
episode 5591.000000, reward total was -3.000000. running mean: -2.263954
episode 5592.000000, reward total was 10.000000. running mean: -2.141314
episode 5593.000000, reward total was 18.000000. running 

episode 5693.000000, reward total was 0.000000. running mean: -1.737634
episode 5694.000000, reward total was -5.000000. running mean: -1.770258
episode 5695.000000, reward total was -13.000000. running mean: -1.882555
episode 5696.000000, reward total was 3.000000. running mean: -1.833729
episode 5697.000000, reward total was -6.000000. running mean: -1.875392
episode 5698.000000, reward total was 3.000000. running mean: -1.826638
episode 5699.000000, reward total was -6.000000. running mean: -1.868372
episode 5700.000000, reward total was 5.000000. running mean: -1.799688
episode 5701.000000, reward total was 1.000000. running mean: -1.771691
episode 5702.000000, reward total was 7.000000. running mean: -1.683974
episode 5703.000000, reward total was -7.000000. running mean: -1.737135
episode 5704.000000, reward total was 2.000000. running mean: -1.699763
episode 5705.000000, reward total was -2.000000. running mean: -1.702766
episode 5706.000000, reward total was -7.000000. running 

episode 5806.000000, reward total was -2.000000. running mean: -1.735111
episode 5807.000000, reward total was 7.000000. running mean: -1.647760
episode 5808.000000, reward total was -3.000000. running mean: -1.661282
episode 5809.000000, reward total was -3.000000. running mean: -1.674670
episode 5810.000000, reward total was -2.000000. running mean: -1.677923
episode 5811.000000, reward total was -3.000000. running mean: -1.691144
episode 5812.000000, reward total was 1.000000. running mean: -1.664232
episode 5813.000000, reward total was -6.000000. running mean: -1.707590
episode 5814.000000, reward total was -6.000000. running mean: -1.750514
episode 5815.000000, reward total was 2.000000. running mean: -1.713009
episode 5816.000000, reward total was -10.000000. running mean: -1.795879
episode 5817.000000, reward total was -5.000000. running mean: -1.827920
episode 5818.000000, reward total was -3.000000. running mean: -1.839641
episode 5819.000000, reward total was 2.000000. runni

episode 5919.000000, reward total was -11.000000. running mean: -1.830679
episode 5920.000000, reward total was -15.000000. running mean: -1.962373
episode 5921.000000, reward total was -1.000000. running mean: -1.952749
episode 5922.000000, reward total was -9.000000. running mean: -2.023221
episode 5923.000000, reward total was 3.000000. running mean: -1.972989
episode 5924.000000, reward total was -1.000000. running mean: -1.963259
episode 5925.000000, reward total was -7.000000. running mean: -2.013627
episode 5926.000000, reward total was 11.000000. running mean: -1.883490
episode 5927.000000, reward total was -6.000000. running mean: -1.924655
episode 5928.000000, reward total was 1.000000. running mean: -1.895409
episode 5929.000000, reward total was 4.000000. running mean: -1.836455
episode 5930.000000, reward total was -6.000000. running mean: -1.878090
episode 5931.000000, reward total was -1.000000. running mean: -1.869309
episode 5932.000000, reward total was 5.000000. runn

In [4]:
play_game(env, model)

C:\Users\User\AppData\Local\Programs\Python\Python310\lib\site-packages\gym\core.py:51: DeprecationWarning: WARN: The argument mode in render method is deprecated; use render_mode during environment initialization instead.
See here for more information: https://www.gymlibrary.ml/content/api/
  deprecation(
C:\Users\User\AppData\Local\Programs\Python\Python310\lib\site-packages\gym\utils\passive_env_checker.py:297: UserWarning: WARN: No render fps was declared in the environment (env.metadata['render_fps'] is None or not defined), rendering may occur at inconsistent fps.
  logger.warn(


Episode finished without success, accumulated reward = 1.0
